In [1]:
kerr_dir = '/work/yifan.wang/ringdown/t12-highermodes/kerr_220_440.ini'
set_toffset = True
events_dir = '/work/yifan.wang/ringdown/t12-highermodes/220_440_5M//events.ini'

In [2]:
import numpy as np
import os,sys,glob,h5py

from pycbc.inference.io import loadfile
from pycbc.workflow import WorkflowConfigParser
from configparser import ConfigParser
from pycbc import pnutils
import lal
from pycbc import coordinates
from pycbc import conversions

# Read SNR file

In [3]:
import json
f = open('/work/yifan.wang/ringdown/snrs.json')
snrs = json.load(f)

In [4]:
events = []
for key in snrs:
    if snrs[key]>4:
        events.append(key)
len(events)

50

# Read in the maxL parameters

In [5]:
def gwinfo(name):
    # read in the 4-OGC posterior files
    #h5file = glob.glob('/work/yifan.wang/4ogc/release_prod/convertsnr/mixed_posterior/'+name+'.hdf')
    h5file = glob.glob('/work/yifan.wang/4ogc/release_prod/convertsnr/1212_posterior/*'+name+'*.hdf')
    # if not found
    #print(h5file)
    if np.size(h5file)!=1:
        print('Error!!! No such file')
        sys.exit(1)
    f = h5py.File(h5file[0],'r')
    # ra, dec, mass
    try:
        maxl_i = np.argmax(f['samples']['maxl_loglr'][:])
    except KeyError:
        print('KeyError')
        sys.exit(1)
    ra = f['samples']['ra'][maxl_i]
    dec = f['samples']['dec'][maxl_i]
    tref = f['samples']['delta_tc'][maxl_i] + f.attrs['trigger_time']
    m1 = f['samples']['srcmass1'][maxl_i]
    m2 = f['samples']['srcmass2'][maxl_i]
    redshift = f['samples']['redshift'][maxl_i]
    mtotal = (m1+m2)*(1+redshift)
    # starting time = merger time + 10 M_f 
    
    spin1_x,spin1_y,spin1_z = coordinates.spherical_to_cartesian(f['samples']['spin1_a'], \
                                                              f['samples']['spin1_azimuthal'],\
                                                              f['samples']['spin1_polar'])
    spin2_x,spin2_y,spin2_z = coordinates.spherical_to_cartesian(f['samples']['spin2_a'], \
                                                              f['samples']['spin2_azimuthal'],\
                                                              f['samples']['spin2_polar'])
    # final mass
    mfsample = conversions.final_mass_from_initial(mass1=f['samples']['srcmass1'],\
                                                   mass2=f['samples']['srcmass2'],\
                                                   spin1x=spin1_x,spin1y=spin1_y,spin1z=spin1_z,\
                                                   spin2x=spin2_x,spin2y=spin2_y,spin2z=spin2_z)
    final_mass = mfsample[maxl_i] * (1+redshift)
    toffset = 5* final_mass * lal.MTSUN_SI
    #final_freq = pnutils.get_final_freq('SEOBNRv4',m1,m2,spin1z,spin2z)
    f.close()
    return ra,dec,tref,mtotal,toffset

# Write the events.ini

In [6]:
# a new file
try:
    os.remove(events_dir)
except FileNotFoundError:
    pass

with open(events_dir, 'w') as t:
    for gwname in events:
        print(gwname)
        ra,dec,tref,mtotal,toffset = gwinfo(gwname)
        
        #1. read in data.ini
        if float(gwname[2:8])<180000:#O1/2 events
            #the o1/2 events' data-GWXXYYZZ.ini files' nameing are kind of complicated.
            #For GWTC-1 events, the name only contains GWYYMMDD, but for o1/2 events detected by 4ogc
            #the naming is GWYYMMDD-HHMMSS, therefore I use "*.ini" trick here
            datadir = glob.glob('/work/yifan.wang/ringdown/t10-4ogc-run/data_config/data-'+str(gwname[:8])+'*.ini')
        else:
            datadir = glob.glob('/work/yifan.wang/ringdown/t10-4ogc-run/data_config/data-'+str(gwname)+'.ini')
            
        if np.size(datadir)==0:
            print('Data config file not found!!!')
            sys.exit(1)
        
        #2. start to write the events.ini
        t.write('[event-'+str(gwname)+']\n')
        t.write('label='+str(gwname)+'\n')
        t.write('config-files='+str(datadir[0])+'\n')
        t.write('\t\t\t'+str(kerr_dir)+'\n')
        t.write('config-overrides =data:trigger-time:'+str(tref)+'\n')
        t.write('\t\t\tstatic_params:ra:'+str(ra)+'\n')
        t.write('\t\t\tstatic_params:dec:'+str(dec)+'\n')
        if mtotal < 150:
            t.write('\t\t\tprior-final_mass:min-final_mass:10\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:300\n')
        else:
            t.write('\t\t\tprior-final_mass:min-final_mass:30\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:500\n')
        # Add toffset
        t.write('\t\t\tstatic_params:toffset:'+str(toffset)+'\n')
            
        #3. add the PSD

        config_dir = glob.glob('/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/*'+gwname[2:]+'*.ini')
        print(config_dir)
        cp = WorkflowConfigParser(config_dir)
        t.write('\t\t\t data:psd-start-time:"'+cp.get('data','psd-start-time')+'" \n')
        t.write('\t\t\t data:psd-end-time:"'+cp.get('data','psd-end-time')+'"\n')
        t.write('\n')
t.close()

GW150914_095045
['/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/inference-GW150914_095045.ini']
GW170104_101158
['/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/inference-GW170104_101158.ini']
GW170121_212536
['/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/inference-GW170121_212536.ini']
GW170403_230611
['/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/inference-GW170403_230611.ini']
GW170727_010430
['/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/inference-GW170727_010430.ini']
GW170729_185629
['/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/inference-GW170729_185629.ini']
GW170809_082821
['/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/inference-GW170809_082821.ini']
GW170814_103043
['/work/yifan.wang/4ogc/release_prod/github-4ogc/inference_configuration/inference-GW170814_103043.ini']
GW170818_022509
['/work/yifan.wa